In [65]:
import pandas as pd
import seaborn as sns
import matplotlib.pyplot as plt
import numpy as np

df= pd.read_csv('C://Users//User//Desktop//MSc Westminster//Dissertation//DataSets//Heart_Disease_Indicators.csv')

In [66]:
from sklearn.model_selection import train_test_split

target_size = 50000

num_class_0 = int(target_size * df['HeartDiseaseorAttack'].value_counts(normalize=True)[0])
num_class_1 = target_size - num_class_0

df_class_0 = df[df['HeartDiseaseorAttack'] == 0]
df_class_1 = df[df['HeartDiseaseorAttack'] == 1]

df_class_0_sampled = df_class_0.sample(n=num_class_0, random_state=15)
df_class_1_sampled = df_class_1.sample(n=num_class_1, random_state=15)

df_sampled = pd.concat([df_class_0_sampled, df_class_1_sampled])

df_sampled = df_sampled.sample(frac=1, random_state=15).reset_index(drop=True)
df= df_sampled
print(df['HeartDiseaseorAttack'].value_counts(normalize=True))

0    0.90582
1    0.09418
Name: HeartDiseaseorAttack, dtype: float64
0    0.90582
1    0.09418
Name: HeartDiseaseorAttack, dtype: float64


In [67]:
df.drop_duplicates(inplace= True)
df.shape

(48050, 22)

(48050, 22)

In [68]:
df= df[df['Diabetes'] != 1].copy()
df.loc[df['Diabetes'] == 2, 'Diabetes'] = 1
print(df['Diabetes'].value_counts())

0    40175
1     6968
Name: Diabetes, dtype: int64
0    40175
1     6968
Name: Diabetes, dtype: int64


In [69]:
categorical_columns= ['HighBP', 'HighChol', 'CholCheck', 'Smoker', 'Stroke', 'Diabetes', 'PhysActivity',
                      'Fruits', 'Veggies', 'HvyAlcoholConsump', 'AnyHealthcare', 'NoDocbcCost', 'DiffWalk',
                      'Sex', 'Age', 'Education', 'Income'
                     ]
df[categorical_columns]= df[categorical_columns].astype(str)
df= pd.get_dummies(df, columns= categorical_columns, drop_first= True)

In [70]:
X= df.drop(['HeartDiseaseorAttack'], axis= 1)
y= df['HeartDiseaseorAttack']

In [71]:
from sklearn.model_selection import train_test_split
X_train, X_test, y_train, y_test= train_test_split(X, y, test_size= 0.2, random_state= 15, stratify= y)

continuous_columns = ['BMI', 'GenHlth', 'MentHlth', 'PhysHlth']

from sklearn.preprocessing import StandardScaler
ss= StandardScaler()
X_train= ss.fit_transform(X_train)
X_test= ss.transform(X_test)

In [72]:
from imblearn.combine import SMOTETomek

smt= SMOTETomek(random_state= 15)
X_sm_tl, y_sm_tl= smt.fit_resample(X_train, y_train)

--- LogisticRegression ---

In [73]:
from sklearn.feature_selection import RFE
from sklearn.metrics import confusion_matrix, classification_report, precision_score, roc_auc_score, accuracy_score
from sklearn.linear_model import LogisticRegression
lr= LogisticRegression(random_state= 15)

selector= RFE(estimator= lr, n_features_to_select=10)
selector= selector.fit(X_sm_tl, y_sm_tl)
selected_features= selector.support_

X_sm_tl_selected= X_sm_tl[:, selected_features]
X_sm_tl_test_selected= X_test[:, selected_features]


lr.fit(X_sm_tl_selected, y_sm_tl)
y_pred_lr= lr.predict(X_sm_tl_test_selected)
y_pred_prob_lr= lr.predict_proba(X_sm_tl_test_selected)[:,1]

cm= confusion_matrix(y_test, y_pred_lr, labels= lr.classes_)
print(classification_report(y_test, y_pred_lr, zero_division=0))
print('Precision:', precision_score(y_test, y_pred_lr, zero_division=0))
print('Accuracy:', accuracy_score(y_test, y_pred_lr))
print('AUC:', roc_auc_score(y_test, y_pred_prob_lr))

              precision    recall  f1-score   support

           0       0.97      0.74      0.84      8517
           1       0.24      0.78      0.37       912

    accuracy                           0.74      9429
   macro avg       0.61      0.76      0.60      9429
weighted avg       0.90      0.74      0.79      9429

Precision: 0.24196855775803144
Accuracy: 0.7431328878990349
AUC: 0.8375662246199037
              precision    recall  f1-score   support

           0       0.97      0.74      0.84      8517
           1       0.24      0.78      0.37       912

    accuracy                           0.74      9429
   macro avg       0.61      0.76      0.60      9429
weighted avg       0.90      0.74      0.79      9429

Precision: 0.24196855775803144
Accuracy: 0.7431328878990349
AUC: 0.8375662246199037


--- DecisionTreeClassifier ---

In [74]:
from sklearn.tree import DecisionTreeClassifier
dt= DecisionTreeClassifier(random_state=15)

selector= RFE(estimator= dt, n_features_to_select=10)
selector= selector.fit(X_sm_tl, y_sm_tl)
selected_features= selector.support_

X_sm_tl_selected= X_sm_tl[:, selected_features]
X_sm_tl_test_selected= X_test[:, selected_features]

dt.fit(X_sm_tl_selected, y_sm_tl)
y_pred_dt= dt.predict(X_sm_tl_test_selected)
y_pred_prob_dt= dt.predict_proba(X_sm_tl_test_selected)[:,1]

cm= confusion_matrix(y_test, y_pred_dt, labels= dt.classes_)
print(classification_report(y_test, y_pred_dt, zero_division=0))
print('Precision:', precision_score(y_test, y_pred_dt, zero_division=0))
print('Accuracy:', accuracy_score(y_test, y_pred_dt))
print('AUC:', roc_auc_score(y_test, y_pred_prob_dt))

              precision    recall  f1-score   support

           0       0.92      0.93      0.93      8517
           1       0.26      0.22      0.24       912

    accuracy                           0.87      9429
   macro avg       0.59      0.58      0.58      9429
weighted avg       0.85      0.87      0.86      9429

Precision: 0.261968085106383
Accuracy: 0.8653091526142751
AUC: 0.5929852755788731
              precision    recall  f1-score   support

           0       0.92      0.93      0.93      8517
           1       0.26      0.22      0.24       912

    accuracy                           0.87      9429
   macro avg       0.59      0.58      0.58      9429
weighted avg       0.85      0.87      0.86      9429

Precision: 0.261968085106383
Accuracy: 0.8653091526142751
AUC: 0.5929852755788731


--- Tuned - DecisionTreeClassifier ---

In [75]:
from sklearn.model_selection import GridSearchCV
param_grid= {
             'max_depth': [None, 10, 20, 30, 40, 50],
             'min_samples_split': [2, 10, 20],
             'min_samples_leaf': [1, 5, 10],
             'max_features': [None, 'sqrt', 'log2'],
             'criterion': ['gini', 'entropy']
            }

gs_dt= GridSearchCV(estimator= dt, param_grid= param_grid, cv= 5, scoring= 'precision')
gs_dt.fit(X_sm_tl, y_sm_tl)

print("Best Parameters:", gs_dt.best_params_)
print("Best Precision Score:", gs_dt.best_score_)

Best Parameters: {'criterion': 'entropy', 'max_depth': None, 'max_features': None, 'min_samples_leaf': 10, 'min_samples_split': 2}
Best Precision Score: 0.9408415474451101
Best Parameters: {'criterion': 'entropy', 'max_depth': None, 'max_features': None, 'min_samples_leaf': 10, 'min_samples_split': 2}
Best Precision Score: 0.9408415474451101


In [76]:
tuned_dt= gs_dt.best_estimator_

selector= RFE(estimator= tuned_dt, n_features_to_select=10)
selector= selector.fit(X_sm_tl, y_sm_tl)
selected_features= selector.support_

X_sm_tl_selected= X_sm_tl[:, selected_features]
X_sm_tl_test_selected= X_test[:, selected_features]
tuned_dt.fit(X_sm_tl_selected, y_sm_tl)

y_pred_tuned_dt= tuned_dt.predict(X_sm_tl_test_selected)
y_pred_prob_tuned_dt= tuned_dt.predict_proba(X_sm_tl_test_selected)[:,1]

cm= confusion_matrix(y_test, y_pred_tuned_dt, labels= tuned_dt.classes_)
print(classification_report(y_test, y_pred_tuned_dt, zero_division=0))
print('Precision:', precision_score(y_test, y_pred_tuned_dt, zero_division=0))
print('Accuracy:', accuracy_score(y_test, y_pred_tuned_dt))
print('AUC:', roc_auc_score(y_test, y_pred_prob_tuned_dt))

              precision    recall  f1-score   support

           0       0.92      0.96      0.94      8517
           1       0.32      0.17      0.22       912

    accuracy                           0.88      9429
   macro avg       0.62      0.57      0.58      9429
weighted avg       0.86      0.88      0.87      9429

Precision: 0.319672131147541
Accuracy: 0.8846113055467175
AUC: 0.7321107269465197
              precision    recall  f1-score   support

           0       0.92      0.96      0.94      8517
           1       0.32      0.17      0.22       912

    accuracy                           0.88      9429
   macro avg       0.62      0.57      0.58      9429
weighted avg       0.86      0.88      0.87      9429

Precision: 0.319672131147541
Accuracy: 0.8846113055467175
AUC: 0.7321107269465197


--- Random Forest ---

In [77]:
from sklearn.ensemble import RandomForestClassifier
rf= RandomForestClassifier(random_state= 15)

selector= RFE(estimator= rf, n_features_to_select=10)
selector= selector.fit(X_sm_tl, y_sm_tl)
selected_features= selector.support_

X_sm_tl_selected= X_sm_tl[:, selected_features]
X_sm_tl_test_selected= X_test[:, selected_features]

rf.fit(X_sm_tl_selected, y_sm_tl)
y_pred_rf= rf.predict(X_sm_tl_test_selected)
y_pred_prob_rf= rf.predict_proba(X_sm_tl_test_selected)[:,1]

In [78]:
cm= confusion_matrix(y_test, y_pred_rf, labels= rf.classes_)
print(classification_report(y_test, y_pred_rf, zero_division=0))
print('Precision:', precision_score(y_test, y_pred_rf, zero_division=0))
print('Accuracy:', accuracy_score(y_test, y_pred_rf))
print('AUC:', roc_auc_score(y_test, y_pred_prob_rf))

              precision    recall  f1-score   support

           0       0.92      0.96      0.94      8517
           1       0.32      0.18      0.23       912

    accuracy                           0.88      9429
   macro avg       0.62      0.57      0.58      9429
weighted avg       0.86      0.88      0.87      9429

Precision: 0.31702544031311153
Accuracy: 0.8834446919079436
AUC: 0.7539362065342998
              precision    recall  f1-score   support

           0       0.92      0.96      0.94      8517
           1       0.32      0.18      0.23       912

    accuracy                           0.88      9429
   macro avg       0.62      0.57      0.58      9429
weighted avg       0.86      0.88      0.87      9429

Precision: 0.31702544031311153
Accuracy: 0.8834446919079436
AUC: 0.7539362065342998


In [79]:
param_grid= {
             'n_estimators': [100, 200, 300],
             'max_depth': [None, 10, 20, 30],
             'min_samples_split': [2, 5, 10],
             'min_samples_leaf': [1, 2, 4],
            }

gs_tuned_rf= GridSearchCV(estimator= rf, param_grid= param_grid, cv= 5, scoring= 'precision', n_jobs= -1, verbose= 2)
gs_tuned_rf.fit(X_sm_tl, y_sm_tl)
print("Best Parameters:", gs_tuned_rf.best_params_)
print("Best Precision Score:", gs_tuned_rf.best_score_)

Fitting 5 folds for each of 108 candidates, totalling 540 fits
Fitting 5 folds for each of 108 candidates, totalling 540 fits
Best Parameters: {'max_depth': None, 'min_samples_leaf': 1, 'min_samples_split': 5, 'n_estimators': 200}
Best Precision Score: 0.9747355169512488
Best Parameters: {'max_depth': None, 'min_samples_leaf': 1, 'min_samples_split': 5, 'n_estimators': 200}
Best Precision Score: 0.9747355169512488


In [80]:
tuned_rf= gs_tuned_rf.best_estimator_

selector= RFE(estimator= tuned_rf, n_features_to_select=10)
selector= selector.fit(X_sm_tl, y_sm_tl)
selected_features= selector.support_

X_sm_tl_selected= X_sm_tl[:, selected_features]
X_sm_tl_test_selected= X_test[:, selected_features]

tuned_rf.fit(X_sm_tl_selected, y_sm_tl)
y_pred_tuned_rf= tuned_rf.predict(X_sm_tl_test_selected)
y_pred_prob_tuned_rf= tuned_rf.predict_proba(X_sm_tl_test_selected)[:,1]

cm= confusion_matrix(y_test, y_pred_tuned_rf, labels= tuned_rf.classes_)
print(classification_report(y_test, y_pred_tuned_rf, zero_division=0))
print('Precision:', precision_score(y_test, y_pred_tuned_rf, zero_division=0))
print('Accuracy:', accuracy_score(y_test, y_pred_tuned_rf))
print('AUC:', roc_auc_score(y_test, y_pred_prob_tuned_rf))

              precision    recall  f1-score   support

           0       0.92      0.97      0.94      8517
           1       0.37      0.17      0.23       912

    accuracy                           0.89      9429
   macro avg       0.64      0.57      0.58      9429
weighted avg       0.86      0.89      0.87      9429

Precision: 0.36561743341404357
Accuracy: 0.8915049315940184
AUC: 0.7723686399131563
              precision    recall  f1-score   support

           0       0.92      0.97      0.94      8517
           1       0.37      0.17      0.23       912

    accuracy                           0.89      9429
   macro avg       0.64      0.57      0.58      9429
weighted avg       0.86      0.89      0.87      9429

Precision: 0.36561743341404357
Accuracy: 0.8915049315940184
AUC: 0.7723686399131563


--- AdaBoost ---

In [81]:
from sklearn.ensemble import AdaBoostClassifier
ada= AdaBoostClassifier(random_state=15)

selector= RFE(estimator= ada, n_features_to_select=10)
selector= selector.fit(X_sm_tl, y_sm_tl)
selected_features= selector.support_

X_sm_tl_selected= X_sm_tl[:, selected_features]
X_sm_tl_test_selected= X_test[:, selected_features]

ada.fit(X_sm_tl_selected, y_sm_tl)
y_pred_ada= ada.predict(X_sm_tl_test_selected)
y_pred_prob_ada= ada.predict_proba(X_sm_tl_test_selected)[:,1]

In [82]:
cm= confusion_matrix(y_test, y_pred_ada, labels= ada.classes_)
print(classification_report(y_test, y_pred_ada, zero_division=0))
print('Precision:', precision_score(y_test, y_pred_ada, zero_division=0))
print('Accuracy:', accuracy_score(y_test, y_pred_ada))
print('AUC:', roc_auc_score(y_test, y_pred_prob_ada))

              precision    recall  f1-score   support

           0       0.93      0.92      0.93      8517
           1       0.35      0.40      0.37       912

    accuracy                           0.87      9429
   macro avg       0.64      0.66      0.65      9429
weighted avg       0.88      0.87      0.87      9429

Precision: 0.34774255523535064
Accuracy: 0.8696574398133419
AUC: 0.8240933638399156
              precision    recall  f1-score   support

           0       0.93      0.92      0.93      8517
           1       0.35      0.40      0.37       912

    accuracy                           0.87      9429
   macro avg       0.64      0.66      0.65      9429
weighted avg       0.88      0.87      0.87      9429

Precision: 0.34774255523535064
Accuracy: 0.8696574398133419
AUC: 0.8240933638399156


In [83]:
param_grid= {'n_estimators': [50, 100, 200]}

gs_ada= GridSearchCV(estimator= ada, param_grid= param_grid, cv= 5, scoring= 'precision', n_jobs= -1, verbose= 2)
gs_ada.fit(X_sm_tl, y_sm_tl)
print("Best Parameters:", gs_ada.best_params_)
print("Best Precision Score:", gs_ada.best_score_)

Fitting 5 folds for each of 3 candidates, totalling 15 fits
Fitting 5 folds for each of 3 candidates, totalling 15 fits
Best Parameters: {'n_estimators': 200}
Best Precision Score: 0.9611136817860977
Best Parameters: {'n_estimators': 200}
Best Precision Score: 0.9611136817860977


In [84]:
tuned_ada= gs_ada.best_estimator_

selector= RFE(estimator= tuned_ada, n_features_to_select=10)
selector= selector.fit(X_sm_tl, y_sm_tl)
selected_features= selector.support_

X_sm_tl_selected= X_sm_tl[:, selected_features]
X_sm_tl_test_selected= X_test[:, selected_features]

tuned_ada.fit(X_sm_tl_selected, y_sm_tl)
y_pred_tuned_ada= tuned_ada.predict(X_sm_tl_test_selected)
y_pred_prob_tuned_ada= tuned_ada.predict_proba(X_sm_tl_test_selected)[:,1]

cm= confusion_matrix(y_test, y_pred_tuned_ada, labels= tuned_ada.classes_)
print(classification_report(y_test, y_pred_tuned_ada, zero_division=0))
print('Precision:', precision_score(y_test, y_pred_tuned_ada, zero_division=0))
print('Accuracy:', accuracy_score(y_test, y_pred_tuned_ada))
print('AUC:', roc_auc_score(y_test, y_pred_prob_tuned_ada))

              precision    recall  f1-score   support

           0       0.92      0.98      0.95      8517
           1       0.44      0.17      0.25       912

    accuracy                           0.90      9429
   macro avg       0.68      0.57      0.60      9429
weighted avg       0.87      0.90      0.88      9429

Precision: 0.43526170798898073
Accuracy: 0.8982925018559762
AUC: 0.8034490230066184
              precision    recall  f1-score   support

           0       0.92      0.98      0.95      8517
           1       0.44      0.17      0.25       912

    accuracy                           0.90      9429
   macro avg       0.68      0.57      0.60      9429
weighted avg       0.87      0.90      0.88      9429

Precision: 0.43526170798898073
Accuracy: 0.8982925018559762
AUC: 0.8034490230066184


--- GradientBoosting ---

In [85]:
from sklearn.ensemble import GradientBoostingClassifier
grb= GradientBoostingClassifier(random_state=15)

selector= RFE(estimator= grb, n_features_to_select=10)
selector= selector.fit(X_sm_tl, y_sm_tl)
selected_features= selector.support_

X_sm_tl_selected= X_sm_tl[:, selected_features]
X_sm_tl_test_selected= X_test[:, selected_features]


grb.fit(X_sm_tl_selected, y_sm_tl)
y_pred_grb= grb.predict(X_sm_tl_test_selected)
y_pred_prob_grb= grb.predict_proba(X_sm_tl_test_selected)[:,1]


cm= confusion_matrix(y_test, y_pred_grb, labels= grb.classes_)
print(classification_report(y_test, y_pred_grb, zero_division=0))
print('Precision:', precision_score(y_test, y_pred_grb, zero_division=0))
print('Accuracy:', accuracy_score(y_test, y_pred_grb))
print('AUC:', roc_auc_score(y_test, y_pred_prob_grb))

              precision    recall  f1-score   support

           0       0.92      0.96      0.94      8517
           1       0.40      0.25      0.31       912

    accuracy                           0.89      9429
   macro avg       0.66      0.61      0.62      9429
weighted avg       0.87      0.89      0.88      9429

Precision: 0.39522998296422485
Accuracy: 0.8902322621699014
AUC: 0.8212241667336123
              precision    recall  f1-score   support

           0       0.92      0.96      0.94      8517
           1       0.40      0.25      0.31       912

    accuracy                           0.89      9429
   macro avg       0.66      0.61      0.62      9429
weighted avg       0.87      0.89      0.88      9429

Precision: 0.39522998296422485
Accuracy: 0.8902322621699014
AUC: 0.8212241667336123


In [86]:
param_grid= {'learning_rate': [0.01, 0.1, 0.2]}

gs_grb= GridSearchCV(estimator= grb, param_grid= param_grid, cv= 5, scoring= 'precision', n_jobs= -1, verbose= 2)
gs_grb.fit(X_sm_tl, y_sm_tl)

print("Best Parameters:", gs_grb.best_params_)
print("Best Precision Score:", gs_grb.best_score_)

Fitting 5 folds for each of 3 candidates, totalling 15 fits
Fitting 5 folds for each of 3 candidates, totalling 15 fits
Best Parameters: {'learning_rate': 0.2}
Best Precision Score: 0.971352205142504
Best Parameters: {'learning_rate': 0.2}
Best Precision Score: 0.971352205142504


In [87]:
tuned_grb= gs_grb.best_estimator_

selector= RFE(estimator= tuned_grb, n_features_to_select=10)
selector= selector.fit(X_sm_tl, y_sm_tl)
selected_features= selector.support_

X_sm_tl_selected= X_sm_tl[:, selected_features]
X_sm_tl_test_selected= X_test[:, selected_features]

tuned_grb.fit(X_sm_tl_selected, y_sm_tl)
y_pred_tuned_grb= tuned_grb.predict(X_sm_tl_test_selected)
y_pred_prob_tuned_grb= tuned_grb.predict_proba(X_sm_tl_test_selected)[:,1]

cm= confusion_matrix(y_test, y_pred_tuned_grb, labels= tuned_grb.classes_)
print(classification_report(y_test, y_pred_tuned_grb, zero_division=0))
print('Precision:', precision_score(y_test, y_pred_tuned_grb, zero_division=0))
print('Accuracy:', accuracy_score(y_test, y_pred_tuned_grb))
print('AUC:', roc_auc_score(y_test, y_pred_prob_tuned_grb))

              precision    recall  f1-score   support

           0       0.91      0.98      0.95      8517
           1       0.44      0.13      0.21       912

    accuracy                           0.90      9429
   macro avg       0.68      0.56      0.58      9429
weighted avg       0.87      0.90      0.87      9429

Precision: 0.4404332129963899
Accuracy: 0.8997772828507795
AUC: 0.819407173784526
              precision    recall  f1-score   support

           0       0.91      0.98      0.95      8517
           1       0.44      0.13      0.21       912

    accuracy                           0.90      9429
   macro avg       0.68      0.56      0.58      9429
weighted avg       0.87      0.90      0.87      9429

Precision: 0.4404332129963899
Accuracy: 0.8997772828507795
AUC: 0.819407173784526


--- XGB ---

In [88]:
from xgboost import XGBClassifier
xgb= XGBClassifier(random_state=15)

selector= RFE(estimator= xgb, n_features_to_select=10)
selector= selector.fit(X_sm_tl, y_sm_tl)
selected_features= selector.support_

X_sm_tl_selected= X_sm_tl[:, selected_features]
X_sm_tl_test_selected= X_test[:, selected_features]

xgb.fit(X_sm_tl_selected, y_sm_tl)
y_pred_xgb= xgb.predict(X_sm_tl_test_selected)
y_pred_prob_xgb= xgb.predict_proba(X_sm_tl_test_selected)[:,1]

cm= confusion_matrix(y_test, y_pred_xgb, labels= xgb.classes_)
print(classification_report(y_test, y_pred_xgb, zero_division=0))
print('Precision:', precision_score(y_test, y_pred_xgb, zero_division=0))
print('Accuracy:', accuracy_score(y_test, y_pred_xgb))
print('AUC:', roc_auc_score(y_test, y_pred_prob_xgb))

              precision    recall  f1-score   support

           0       0.91      0.99      0.95      8517
           1       0.46      0.10      0.16       912

    accuracy                           0.90      9429
   macro avg       0.68      0.54      0.55      9429
weighted avg       0.87      0.90      0.87      9429

Precision: 0.45789473684210524
Accuracy: 0.901580231201612
AUC: 0.804015807394499
              precision    recall  f1-score   support

           0       0.91      0.99      0.95      8517
           1       0.46      0.10      0.16       912

    accuracy                           0.90      9429
   macro avg       0.68      0.54      0.55      9429
weighted avg       0.87      0.90      0.87      9429

Precision: 0.45789473684210524
Accuracy: 0.901580231201612
AUC: 0.804015807394499


In [89]:
params_XGBoost= {'learning_rate': [0.01, 0.1, 1.0]}

gs_xgb= GridSearchCV(estimator= xgb, param_grid= params_XGBoost, cv= 5, scoring= 'precision', n_jobs= -1, verbose= 2)
gs_xgb.fit(X_sm_tl, y_sm_tl)

print("Best Parameters:", gs_xgb.best_params_)
print("Best Precision Score:", gs_xgb.best_score_)

tuned_xgb= gs_xgb.best_estimator_

selector= RFE(estimator= tuned_xgb, n_features_to_select=10)
selector= selector.fit(X_sm_tl, y_sm_tl)
selected_features= selector.support_

X_sm_tl_selected= X_sm_tl[:, selected_features]
X_sm_tl_test_selected= X_test[:, selected_features]

tuned_xgb.fit(X_sm_tl_selected, y_sm_tl)
y_pred_tuned_xgb= tuned_xgb.predict(X_sm_tl_test_selected)
y_pred_prob_tuned_xgb= tuned_xgb.predict_proba(X_sm_tl_test_selected)[:,1]

cm= confusion_matrix(y_test, y_pred_tuned_xgb, labels= tuned_xgb.classes_)
print(classification_report(y_test, y_pred_tuned_xgb, zero_division=0))
print('Precision:', precision_score(y_test, y_pred_tuned_xgb, zero_division=0))
print('Accuracy:', accuracy_score(y_test, y_pred_tuned_xgb))
print('AUC:', roc_auc_score(y_test, y_pred_prob_tuned_xgb))

Fitting 5 folds for each of 3 candidates, totalling 15 fits
Fitting 5 folds for each of 3 candidates, totalling 15 fits
Best Parameters: {'learning_rate': 0.1}
Best Precision Score: 0.9687437596374279
Best Parameters: {'learning_rate': 0.1}
Best Precision Score: 0.9687437596374279
              precision    recall  f1-score   support

           0       0.91      0.98      0.95      8517
           1       0.42      0.13      0.20       912

    accuracy                           0.90      9429
   macro avg       0.67      0.56      0.57      9429
weighted avg       0.87      0.90      0.87      9429

Precision: 0.42142857142857143
Accuracy: 0.8986106692120055
AUC: 0.816064079271797
              precision    recall  f1-score   support

           0       0.91      0.98      0.95      8517
           1       0.42      0.13      0.20       912

    accuracy                           0.90      9429
   macro avg       0.67      0.56      0.57      9429
weighted avg       0.87      0.90   

--- LGBM ---

In [90]:
from lightgbm import LGBMClassifier
lgm= LGBMClassifier(random_state=15)

selector= RFE(estimator= lgm, n_features_to_select=10)
selector= selector.fit(X_sm_tl, y_sm_tl)
selected_features= selector.support_

X_sm_tl_selected= X_sm_tl[:, selected_features]
X_sm_tl_test_selected= X_test[:, selected_features]


lgm.fit(X_sm_tl_selected, y_sm_tl)
y_pred_lgm= lgm.predict(X_sm_tl_test_selected)
y_pred_prob_lgm= lgm.predict_proba(X_sm_tl_test_selected)[:,1]

cm= confusion_matrix(y_test, y_pred_lgm, labels= lgm.classes_)
print(classification_report(y_test, y_pred_lgm, zero_division=0))
print('Precision:', precision_score(y_test, y_pred_lgm, zero_division=0))
print('Accuracy:', accuracy_score(y_test, y_pred_lgm))
print('AUC:', roc_auc_score(y_test, y_pred_prob_lgm))

[LightGBM] [Info] Number of positive: 33993, number of negative: 33993
[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.009833 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 8572
[LightGBM] [Info] Number of data points in the train set: 67986, number of used features: 42
[LightGBM] [Info] [binary:BoostFromScore]: pavg=0.500000 -> initscore=0.000000
[LightGBM] [Info] Number of positive: 33993, number of negative: 33993
[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.009833 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 8572
[LightGBM] [Info] Number of data points in the train set: 67986, number of used features: 42
[LightGBM] [Info] [binary:BoostFromScore]: pavg=0.500000 -> initscore=0.0

[LightGBM] [Info] Number of positive: 33993, number of negative: 33993
[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.007814 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 7664
[LightGBM] [Info] Number of data points in the train set: 67986, number of used features: 34
[LightGBM] [Info] [binary:BoostFromScore]: pavg=0.500000 -> initscore=0.000000
[LightGBM] [Info] Number of positive: 33993, number of negative: 33993
[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.005344 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 7594
[LightGBM] [Info] Number of data points in the train set: 67986, number of used features: 33
[LightGBM] [Info] [binary:BoostFromScore]: pavg=0.500000 -> initscore=0.0

[LightGBM] [Info] Number of positive: 33993, number of negative: 33993
[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.004897 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 6202
[LightGBM] [Info] Number of data points in the train set: 67986, number of used features: 25
[LightGBM] [Info] [binary:BoostFromScore]: pavg=0.500000 -> initscore=0.000000
[LightGBM] [Info] Number of positive: 33993, number of negative: 33993
[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.004897 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 6202
[LightGBM] [Info] Number of data points in the train set: 67986, number of used features: 25
[LightGBM] [Info] [binary:BoostFromScore]: pavg=0.500000 -> initscore=0.0

[LightGBM] [Info] Number of positive: 33993, number of negative: 33993
[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.004162 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 4335
[LightGBM] [Info] Number of data points in the train set: 67986, number of used features: 17
[LightGBM] [Info] [binary:BoostFromScore]: pavg=0.500000 -> initscore=0.000000
[LightGBM] [Info] Number of positive: 33993, number of negative: 33993
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.005079 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 4080
[LightGBM] [Info] Number of data points in the train set: 67986, number of used features: 16
[LightGBM] [Info] [binary:BoostFromScore]: pavg=0.500000 -> initscore=0.000000
[LightGBM] [Info] Number of positive: 33993, number of neg

In [91]:
params_LGB= {'learning_rate': [0.001, 0.01, 0.1, 1.0],
             'num_leaves': [31, 127],
             'reg_alpha': [0.1, 0.5],
             'min_data_in_leaf': [30, 50, 100, 300, 400]}

gs_lgm= GridSearchCV(estimator= lgm, param_grid= params_LGB, cv=5, scoring='precision', n_jobs=-1, verbose=2)
gs_lgm.fit(X_sm_tl, y_sm_tl)

print("Best Parameters:", gs_lgm.best_params_)
print("Best Precision Score:", gs_lgm.best_score_)

tuned_lgm= gs_lgm.best_estimator_

selector= RFE(estimator= tuned_lgm, n_features_to_select=10)
selector= selector.fit(X_sm_tl, y_sm_tl)
selected_features= selector.support_

X_sm_tl_selected= X_sm_tl[:, selected_features]
X_sm_tl_test_selected= X_test[:, selected_features]

tuned_lgm.fit(X_sm_tl_selected, y_sm_tl)

y_pred_tuned_lgm= tuned_lgm.predict(X_sm_tl_test_selected)
y_pred_prob_tuned_lgm= tuned_lgm.predict_proba(X_sm_tl_test_selected)[:,1]

cm= confusion_matrix(y_test, y_pred_tuned_lgm, labels= tuned_lgm.classes_)
print(classification_report(y_test, y_pred_tuned_lgm, zero_division=0))
print('Precision:', precision_score(y_test, y_pred_tuned_lgm, zero_division=0))
print('Accuracy:', accuracy_score(y_test, y_pred_tuned_lgm))
print('AUC:', roc_auc_score(y_test, y_pred_prob_tuned_lgm))

Fitting 5 folds for each of 80 candidates, totalling 400 fits
Fitting 5 folds for each of 80 candidates, totalling 400 fits
[LightGBM] [Warning] min_data_in_leaf is set=300, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=300
[LightGBM] [Warning] min_data_in_leaf is set=300, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=300
[LightGBM] [Warning] min_data_in_leaf is set=300, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=300
[LightGBM] [Warning] min_data_in_leaf is set=300, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=300
[LightGBM] [Info] Number of positive: 33993, number of negative: 33993
[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.007884 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 8572
[LightGBM] [Info] Number of data points in the tr

[LightGBM] [Warning] min_data_in_leaf is set=300, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=300
[LightGBM] [Warning] min_data_in_leaf is set=300, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=300
[LightGBM] [Info] Number of positive: 33993, number of negative: 33993
[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.006574 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 8443
[LightGBM] [Info] Number of data points in the train set: 67986, number of used features: 38
[LightGBM] [Info] [binary:BoostFromScore]: pavg=0.500000 -> initscore=0.000000
[LightGBM] [Warning] min_data_in_leaf is set=300, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=300
[LightGBM] [Warning] min_data_in_leaf is set=300, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=300
[

[LightGBM] [Warning] min_data_in_leaf is set=300, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=300
[LightGBM] [Warning] min_data_in_leaf is set=300, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=300
[LightGBM] [Info] Number of positive: 33993, number of negative: 33993
[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.005268 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 7393
[LightGBM] [Info] Number of data points in the train set: 67986, number of used features: 32
[LightGBM] [Info] [binary:BoostFromScore]: pavg=0.500000 -> initscore=0.000000
[LightGBM] [Warning] min_data_in_leaf is set=300, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=300
[LightGBM] [Warning] min_data_in_leaf is set=300, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=300
[

[LightGBM] [Warning] min_data_in_leaf is set=300, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=300
[LightGBM] [Warning] min_data_in_leaf is set=300, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=300
[LightGBM] [Info] Number of positive: 33993, number of negative: 33993
[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.004633 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 6712
[LightGBM] [Info] Number of data points in the train set: 67986, number of used features: 27
[LightGBM] [Info] [binary:BoostFromScore]: pavg=0.500000 -> initscore=0.000000
[LightGBM] [Warning] min_data_in_leaf is set=300, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=300
[LightGBM] [Warning] min_data_in_leaf is set=300, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=300
[

[LightGBM] [Warning] min_data_in_leaf is set=300, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=300
[LightGBM] [Warning] min_data_in_leaf is set=300, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=300
[LightGBM] [Info] Number of positive: 33993, number of negative: 33993
[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.003755 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 5182
[LightGBM] [Info] Number of data points in the train set: 67986, number of used features: 21
[LightGBM] [Info] [binary:BoostFromScore]: pavg=0.500000 -> initscore=0.000000
[LightGBM] [Warning] min_data_in_leaf is set=300, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=300
[LightGBM] [Warning] min_data_in_leaf is set=300, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=300
[

[LightGBM] [Warning] min_data_in_leaf is set=300, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=300
[LightGBM] [Warning] min_data_in_leaf is set=300, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=300
[LightGBM] [Info] Number of positive: 33993, number of negative: 33993
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.006336 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 3825
[LightGBM] [Info] Number of data points in the train set: 67986, number of used features: 15
[LightGBM] [Info] [binary:BoostFromScore]: pavg=0.500000 -> initscore=0.000000
[LightGBM] [Warning] min_data_in_leaf is set=300, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=300
[LightGBM] [Warning] min_data_in_leaf is set=300, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=300
[LightGBM] [Info] Number of positive: 33993, number of negative: 

[LightGBM] [Warning] min_data_in_leaf is set=300, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=300
[LightGBM] [Warning] min_data_in_leaf is set=300, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=300
[LightGBM] [Info] Number of positive: 33993, number of negative: 33993
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.002607 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 2550
[LightGBM] [Info] Number of data points in the train set: 67986, number of used features: 10
[LightGBM] [Info] [binary:BoostFromScore]: pavg=0.500000 -> initscore=0.000000
[LightGBM] [Warning] min_data_in_leaf is set=300, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=300
[LightGBM] [Warning] min_data_in_leaf is set=300, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=300
[LightGBM] [Info] Number of positive: 33993, number of negative: 

--- CatBoost ---

In [92]:
from catboost import CatBoostClassifier
cat= CatBoostClassifier(random_state=15)

selector= RFE(estimator= cat, n_features_to_select=10)
selector= selector.fit(X_sm_tl, y_sm_tl)
selected_features= selector.support_

X_sm_tl_selected= X_sm_tl[:, selected_features]
X_sm_tl_test_selected= X_test[:, selected_features]

cat.fit(X_sm_tl_selected, y_sm_tl)
y_pred_cat= cat.predict(X_sm_tl_test_selected)
y_pred_prob_cat= cat.predict_proba(X_sm_tl_test_selected)[:,1]

cm= confusion_matrix(y_test, y_pred_cat, labels= cat.classes_)
print(classification_report(y_test, y_pred_cat, zero_division=0))
print('Precision:', precision_score(y_test, y_pred_cat, zero_division=0))
print('Accuracy:', accuracy_score(y_test, y_pred_cat))
print('AUC:', roc_auc_score(y_test, y_pred_prob_cat))

Learning rate set to 0.062428
0:	learn: 0.6250216	total: 22.9ms	remaining: 22.9s
Learning rate set to 0.062428
0:	learn: 0.6250216	total: 22.9ms	remaining: 22.9s
1:	learn: 0.5692396	total: 47ms	remaining: 23.4s
2:	learn: 0.5267455	total: 70.7ms	remaining: 23.5s
3:	learn: 0.4884263	total: 92.3ms	remaining: 23s
4:	learn: 0.4548822	total: 117ms	remaining: 23.4s
5:	learn: 0.4285898	total: 140ms	remaining: 23.2s
6:	learn: 0.4089582	total: 162ms	remaining: 22.9s
7:	learn: 0.3917242	total: 183ms	remaining: 22.7s
1:	learn: 0.5692396	total: 47ms	remaining: 23.4s
2:	learn: 0.5267455	total: 70.7ms	remaining: 23.5s
3:	learn: 0.4884263	total: 92.3ms	remaining: 23s
4:	learn: 0.4548822	total: 117ms	remaining: 23.4s
5:	learn: 0.4285898	total: 140ms	remaining: 23.2s
6:	learn: 0.4089582	total: 162ms	remaining: 22.9s
7:	learn: 0.3917242	total: 183ms	remaining: 22.7s
8:	learn: 0.3741989	total: 205ms	remaining: 22.6s
9:	learn: 0.3594983	total: 227ms	remaining: 22.5s
8:	learn: 0.3741989	total: 205ms	remaini

83:	learn: 0.1724446	total: 2.08s	remaining: 22.6s
84:	learn: 0.1718136	total: 2.1s	remaining: 22.6s
85:	learn: 0.1710160	total: 2.12s	remaining: 22.5s
83:	learn: 0.1724446	total: 2.08s	remaining: 22.6s
84:	learn: 0.1718136	total: 2.1s	remaining: 22.6s
85:	learn: 0.1710160	total: 2.12s	remaining: 22.5s
86:	learn: 0.1703846	total: 2.14s	remaining: 22.5s
87:	learn: 0.1702529	total: 2.16s	remaining: 22.4s
88:	learn: 0.1698448	total: 2.19s	remaining: 22.4s
89:	learn: 0.1694474	total: 2.21s	remaining: 22.4s
90:	learn: 0.1691821	total: 2.23s	remaining: 22.3s
86:	learn: 0.1703846	total: 2.14s	remaining: 22.5s
87:	learn: 0.1702529	total: 2.16s	remaining: 22.4s
88:	learn: 0.1698448	total: 2.19s	remaining: 22.4s
89:	learn: 0.1694474	total: 2.21s	remaining: 22.4s
90:	learn: 0.1691821	total: 2.23s	remaining: 22.3s
91:	learn: 0.1690380	total: 2.26s	remaining: 22.3s
92:	learn: 0.1689361	total: 2.3s	remaining: 22.4s
93:	learn: 0.1684170	total: 2.32s	remaining: 22.4s
91:	learn: 0.1690380	total: 2.26s	

161:	learn: 0.1556985	total: 3.78s	remaining: 19.6s
162:	learn: 0.1550086	total: 3.81s	remaining: 19.6s
163:	learn: 0.1549262	total: 3.83s	remaining: 19.5s
164:	learn: 0.1545799	total: 3.85s	remaining: 19.5s
165:	learn: 0.1545041	total: 3.88s	remaining: 19.5s
166:	learn: 0.1543881	total: 3.89s	remaining: 19.4s
167:	learn: 0.1541451	total: 3.92s	remaining: 19.4s
168:	learn: 0.1540455	total: 3.94s	remaining: 19.4s
169:	learn: 0.1539882	total: 3.95s	remaining: 19.3s
167:	learn: 0.1541451	total: 3.92s	remaining: 19.4s
168:	learn: 0.1540455	total: 3.94s	remaining: 19.4s
169:	learn: 0.1539882	total: 3.95s	remaining: 19.3s
170:	learn: 0.1538743	total: 3.98s	remaining: 19.3s
171:	learn: 0.1537996	total: 4s	remaining: 19.2s
172:	learn: 0.1537200	total: 4.02s	remaining: 19.2s
173:	learn: 0.1529509	total: 4.04s	remaining: 19.2s
174:	learn: 0.1526168	total: 4.06s	remaining: 19.1s
175:	learn: 0.1524008	total: 4.08s	remaining: 19.1s
176:	learn: 0.1520775	total: 4.1s	remaining: 19s
170:	learn: 0.1538

240:	learn: 0.1414963	total: 5.43s	remaining: 17.1s
241:	learn: 0.1412653	total: 5.45s	remaining: 17.1s
242:	learn: 0.1411834	total: 5.47s	remaining: 17s
243:	learn: 0.1411171	total: 5.49s	remaining: 17s
244:	learn: 0.1410060	total: 5.5s	remaining: 17s
245:	learn: 0.1409423	total: 5.52s	remaining: 16.9s
246:	learn: 0.1408889	total: 5.54s	remaining: 16.9s
247:	learn: 0.1408427	total: 5.56s	remaining: 16.9s
248:	learn: 0.1406808	total: 5.58s	remaining: 16.8s
249:	learn: 0.1406234	total: 5.6s	remaining: 16.8s
250:	learn: 0.1405499	total: 5.62s	remaining: 16.8s
249:	learn: 0.1406234	total: 5.6s	remaining: 16.8s
250:	learn: 0.1405499	total: 5.62s	remaining: 16.8s
251:	learn: 0.1404933	total: 5.64s	remaining: 16.7s
252:	learn: 0.1403168	total: 5.66s	remaining: 16.7s
253:	learn: 0.1402387	total: 5.68s	remaining: 16.7s
254:	learn: 0.1401755	total: 5.7s	remaining: 16.7s
255:	learn: 0.1401162	total: 5.72s	remaining: 16.6s
256:	learn: 0.1400659	total: 5.74s	remaining: 16.6s
257:	learn: 0.1400201	

323:	learn: 0.1353511	total: 7.3s	remaining: 15.2s
324:	learn: 0.1352748	total: 7.33s	remaining: 15.2s
325:	learn: 0.1352162	total: 7.35s	remaining: 15.2s
326:	learn: 0.1351592	total: 7.38s	remaining: 15.2s
327:	learn: 0.1351203	total: 7.4s	remaining: 15.2s
328:	learn: 0.1350572	total: 7.43s	remaining: 15.1s
329:	learn: 0.1349899	total: 7.45s	remaining: 15.1s
330:	learn: 0.1349296	total: 7.47s	remaining: 15.1s
331:	learn: 0.1348878	total: 7.5s	remaining: 15.1s
326:	learn: 0.1351592	total: 7.38s	remaining: 15.2s
327:	learn: 0.1351203	total: 7.4s	remaining: 15.2s
328:	learn: 0.1350572	total: 7.43s	remaining: 15.1s
329:	learn: 0.1349899	total: 7.45s	remaining: 15.1s
330:	learn: 0.1349296	total: 7.47s	remaining: 15.1s
331:	learn: 0.1348878	total: 7.5s	remaining: 15.1s
332:	learn: 0.1347668	total: 7.52s	remaining: 15.1s
333:	learn: 0.1347230	total: 7.54s	remaining: 15s
334:	learn: 0.1345956	total: 7.56s	remaining: 15s
332:	learn: 0.1347668	total: 7.52s	remaining: 15.1s
333:	learn: 0.1347230

...

648:	learn: 0.1390349	total: 9.8s	remaining: 5.3s
649:	learn: 0.1390044	total: 9.81s	remaining: 5.29s
650:	learn: 0.1389881	total: 9.83s	remaining: 5.27s
651:	learn: 0.1389591	total: 9.84s	remaining: 5.25s
652:	learn: 0.1389417	total: 9.86s	remaining: 5.24s
653:	learn: 0.1389202	total: 9.87s	remaining: 5.22s
654:	learn: 0.1388819	total: 9.88s	remaining: 5.21s
655:	learn: 0.1388578	total: 9.9s	remaining: 5.19s
656:	learn: 0.1388455	total: 9.91s	remaining: 5.17s
657:	learn: 0.1388343	total: 9.93s	remaining: 5.16s
658:	learn: 0.1388215	total: 9.94s	remaining: 5.14s
659:	learn: 0.1388017	total: 9.96s	remaining: 5.13s
660:	learn: 0.1387806	total: 9.97s	remaining: 5.11s
661:	learn: 0.1387626	total: 9.98s	remaining: 5.1s
648:	learn: 0.1390349	total: 9.8s	remaining: 5.3s
649:	learn: 0.1390044	total: 9.81s	remaining: 5.29s
650:	learn: 0.1389881	total: 9.83s	remaining: 5.27s
651:	learn: 0.1389591	total: 9.84s	remaining: 5.25s
652:	learn: 0.1389417	total: 9.86s	remaining: 5.24s
653:	learn: 0.1389

731:	learn: 0.1372540	total: 11s	remaining: 4.03s
732:	learn: 0.1372400	total: 11s	remaining: 4.01s
733:	learn: 0.1372135	total: 11s	remaining: 4s
734:	learn: 0.1371956	total: 11.1s	remaining: 3.98s
735:	learn: 0.1371834	total: 11.1s	remaining: 3.97s
736:	learn: 0.1371630	total: 11.1s	remaining: 3.95s
737:	learn: 0.1371413	total: 11.1s	remaining: 3.94s
738:	learn: 0.1371244	total: 11.1s	remaining: 3.92s
739:	learn: 0.1371030	total: 11.1s	remaining: 3.91s
740:	learn: 0.1370886	total: 11.1s	remaining: 3.89s
741:	learn: 0.1370632	total: 11.1s	remaining: 3.88s
742:	learn: 0.1370469	total: 11.2s	remaining: 3.86s
743:	learn: 0.1370223	total: 11.2s	remaining: 3.85s
744:	learn: 0.1370018	total: 11.2s	remaining: 3.83s
731:	learn: 0.1372540	total: 11s	remaining: 4.03s
732:	learn: 0.1372400	total: 11s	remaining: 4.01s
733:	learn: 0.1372135	total: 11s	remaining: 4s
734:	learn: 0.1371956	total: 11.1s	remaining: 3.98s
735:	learn: 0.1371834	total: 11.1s	remaining: 3.97s
736:	learn: 0.1371630	total: 1

814:	learn: 0.1355959	total: 12.2s	remaining: 2.77s
815:	learn: 0.1355633	total: 12.2s	remaining: 2.75s
816:	learn: 0.1355437	total: 12.2s	remaining: 2.74s
817:	learn: 0.1355273	total: 12.2s	remaining: 2.72s
818:	learn: 0.1355114	total: 12.3s	remaining: 2.71s
819:	learn: 0.1354962	total: 12.3s	remaining: 2.69s
820:	learn: 0.1354791	total: 12.3s	remaining: 2.68s
821:	learn: 0.1354614	total: 12.3s	remaining: 2.67s
822:	learn: 0.1354399	total: 12.3s	remaining: 2.65s
823:	learn: 0.1354243	total: 12.3s	remaining: 2.63s
824:	learn: 0.1354060	total: 12.3s	remaining: 2.62s
825:	learn: 0.1353927	total: 12.4s	remaining: 2.6s
826:	learn: 0.1353721	total: 12.4s	remaining: 2.59s
827:	learn: 0.1353473	total: 12.4s	remaining: 2.57s
814:	learn: 0.1355959	total: 12.2s	remaining: 2.77s
815:	learn: 0.1355633	total: 12.2s	remaining: 2.75s
816:	learn: 0.1355437	total: 12.2s	remaining: 2.74s
817:	learn: 0.1355273	total: 12.2s	remaining: 2.72s
818:	learn: 0.1355114	total: 12.3s	remaining: 2.71s
819:	learn: 0

900:	learn: 0.1341571	total: 13.4s	remaining: 1.47s
901:	learn: 0.1341271	total: 13.4s	remaining: 1.46s
902:	learn: 0.1341108	total: 13.4s	remaining: 1.44s
903:	learn: 0.1340875	total: 13.5s	remaining: 1.43s
904:	learn: 0.1340712	total: 13.5s	remaining: 1.41s
905:	learn: 0.1340488	total: 13.5s	remaining: 1.4s
906:	learn: 0.1340368	total: 13.5s	remaining: 1.38s
907:	learn: 0.1340267	total: 13.5s	remaining: 1.37s
908:	learn: 0.1339992	total: 13.5s	remaining: 1.35s
909:	learn: 0.1339864	total: 13.5s	remaining: 1.34s
910:	learn: 0.1339752	total: 13.6s	remaining: 1.32s
911:	learn: 0.1339623	total: 13.6s	remaining: 1.31s
912:	learn: 0.1339537	total: 13.6s	remaining: 1.29s
913:	learn: 0.1339336	total: 13.6s	remaining: 1.28s
900:	learn: 0.1341571	total: 13.4s	remaining: 1.47s
901:	learn: 0.1341271	total: 13.4s	remaining: 1.46s
902:	learn: 0.1341108	total: 13.4s	remaining: 1.44s
903:	learn: 0.1340875	total: 13.5s	remaining: 1.43s
904:	learn: 0.1340712	total: 13.5s	remaining: 1.41s
905:	learn: 0

983:	learn: 0.1328434	total: 14.6s	remaining: 238ms
984:	learn: 0.1328282	total: 14.6s	remaining: 223ms
985:	learn: 0.1328193	total: 14.6s	remaining: 208ms
986:	learn: 0.1328045	total: 14.7s	remaining: 193ms
987:	learn: 0.1327843	total: 14.7s	remaining: 178ms
988:	learn: 0.1327716	total: 14.7s	remaining: 163ms
989:	learn: 0.1327479	total: 14.7s	remaining: 149ms
990:	learn: 0.1327395	total: 14.7s	remaining: 134ms
991:	learn: 0.1327318	total: 14.7s	remaining: 119ms
992:	learn: 0.1327149	total: 14.8s	remaining: 104ms
993:	learn: 0.1326970	total: 14.8s	remaining: 89.1ms
994:	learn: 0.1326749	total: 14.8s	remaining: 74.3ms
995:	learn: 0.1326566	total: 14.8s	remaining: 59.4ms
996:	learn: 0.1326442	total: 14.8s	remaining: 44.6ms
983:	learn: 0.1328434	total: 14.6s	remaining: 238ms
984:	learn: 0.1328282	total: 14.6s	remaining: 223ms
985:	learn: 0.1328193	total: 14.6s	remaining: 208ms
986:	learn: 0.1328045	total: 14.7s	remaining: 193ms
987:	learn: 0.1327843	total: 14.7s	remaining: 178ms
988:	lea

In [93]:
params_CatBoost= {
                  'depth': [3,5,10],
                  'learning_rate' : [0.01,0.1,1],
                  'iterations' : [5,10,50,100]
                 }

gs_cat= GridSearchCV(estimator= cat, param_grid= params_CatBoost, cv=5, scoring='precision', n_jobs=-1, verbose=2)
gs_cat.fit(X_sm_tl, y_sm_tl)

print("Best Parameters:", gs_cat.best_params_)
print("Best Precision Score:", gs_cat.best_score_)

tuned_cat= gs_cat.best_estimator_

selector= RFE(estimator= tuned_cat, n_features_to_select=10)
selector= selector.fit(X_sm_tl, y_sm_tl)
selected_features= selector.support_

X_sm_tl_selected= X_sm_tl[:, selected_features]
X_sm_tl_test_selected= X_test[:, selected_features]

tuned_cat.fit(X_sm_tl_selected, y_sm_tl)
y_pred_tuned_cat= tuned_cat.predict(X_sm_tl_test_selected)
y_pred_prob_tuned_cat= tuned_cat.predict_proba(X_sm_tl_test_selected)[:,1]

cm= confusion_matrix(y_test, y_pred_tuned_cat, labels= tuned_cat.classes_)
print(classification_report(y_test, y_pred_tuned_cat, zero_division=0))
print('Precision:', precision_score(y_test, y_pred_tuned_cat, zero_division=0))
print('Accuracy:', accuracy_score(y_test, y_pred_tuned_cat))
print('AUC:', roc_auc_score(y_test, y_pred_prob_tuned_cat))

Fitting 5 folds for each of 36 candidates, totalling 180 fits
Fitting 5 folds for each of 36 candidates, totalling 180 fits
0:	learn: 0.4923625	total: 14.1ms	remaining: 692ms
1:	learn: 0.4102545	total: 30.6ms	remaining: 734ms
2:	learn: 0.3467355	total: 49.6ms	remaining: 776ms
3:	learn: 0.2992550	total: 68.1ms	remaining: 783ms
4:	learn: 0.2826226	total: 82.8ms	remaining: 745ms
5:	learn: 0.2584881	total: 104ms	remaining: 762ms
6:	learn: 0.2322352	total: 119ms	remaining: 730ms
7:	learn: 0.2252604	total: 133ms	remaining: 699ms
8:	learn: 0.2194321	total: 147ms	remaining: 671ms
9:	learn: 0.2123800	total: 162ms	remaining: 647ms
10:	learn: 0.1999490	total: 180ms	remaining: 638ms
11:	learn: 0.1915375	total: 198ms	remaining: 627ms
0:	learn: 0.4923625	total: 14.1ms	remaining: 692ms
1:	learn: 0.4102545	total: 30.6ms	remaining: 734ms
2:	learn: 0.3467355	total: 49.6ms	remaining: 776ms
3:	learn: 0.2992550	total: 68.1ms	remaining: 783ms
4:	learn: 0.2826226	total: 82.8ms	remaining: 745ms
5:	learn: 0.25

30:	learn: 0.1490579	total: 422ms	remaining: 259ms
31:	learn: 0.1484102	total: 433ms	remaining: 243ms
32:	learn: 0.1476666	total: 445ms	remaining: 229ms
33:	learn: 0.1463616	total: 459ms	remaining: 216ms
34:	learn: 0.1462107	total: 474ms	remaining: 203ms
35:	learn: 0.1460656	total: 488ms	remaining: 190ms
36:	learn: 0.1458348	total: 503ms	remaining: 177ms
37:	learn: 0.1445214	total: 518ms	remaining: 164ms
38:	learn: 0.1442947	total: 530ms	remaining: 149ms
39:	learn: 0.1440775	total: 544ms	remaining: 136ms
40:	learn: 0.1435968	total: 556ms	remaining: 122ms
41:	learn: 0.1435303	total: 568ms	remaining: 108ms
42:	learn: 0.1431038	total: 581ms	remaining: 94.6ms
43:	learn: 0.1429679	total: 592ms	remaining: 80.8ms
44:	learn: 0.1427063	total: 604ms	remaining: 67.1ms
30:	learn: 0.1490579	total: 422ms	remaining: 259ms
31:	learn: 0.1484102	total: 433ms	remaining: 243ms
32:	learn: 0.1476666	total: 445ms	remaining: 229ms
33:	learn: 0.1463616	total: 459ms	remaining: 216ms
34:	learn: 0.1462107	total: 

16:	learn: 0.1705126	total: 210ms	remaining: 407ms
17:	learn: 0.1647320	total: 221ms	remaining: 394ms
18:	learn: 0.1634533	total: 233ms	remaining: 380ms
19:	learn: 0.1581059	total: 244ms	remaining: 366ms
20:	learn: 0.1575463	total: 255ms	remaining: 353ms
21:	learn: 0.1567177	total: 266ms	remaining: 338ms
22:	learn: 0.1563917	total: 279ms	remaining: 327ms
23:	learn: 0.1552909	total: 289ms	remaining: 314ms
24:	learn: 0.1530390	total: 300ms	remaining: 300ms
25:	learn: 0.1509681	total: 313ms	remaining: 289ms
26:	learn: 0.1506446	total: 323ms	remaining: 275ms
27:	learn: 0.1503245	total: 335ms	remaining: 263ms
28:	learn: 0.1489292	total: 347ms	remaining: 251ms
29:	learn: 0.1486714	total: 358ms	remaining: 239ms
30:	learn: 0.1485214	total: 369ms	remaining: 226ms
31:	learn: 0.1481735	total: 379ms	remaining: 213ms
32:	learn: 0.1477364	total: 391ms	remaining: 201ms
16:	learn: 0.1705126	total: 210ms	remaining: 407ms
17:	learn: 0.1647320	total: 221ms	remaining: 394ms
18:	learn: 0.1634533	total: 233

49:	learn: 0.1427972	total: 601ms	remaining: 0us
0:	learn: 0.4821317	total: 15.6ms	remaining: 763ms
1:	learn: 0.3957770	total: 29.5ms	remaining: 708ms
2:	learn: 0.3222090	total: 44ms	remaining: 689ms
49:	learn: 0.1427972	total: 601ms	remaining: 0us
0:	learn: 0.4821317	total: 15.6ms	remaining: 763ms
1:	learn: 0.3957770	total: 29.5ms	remaining: 708ms
2:	learn: 0.3222090	total: 44ms	remaining: 689ms
3:	learn: 0.2764971	total: 59.4ms	remaining: 684ms
4:	learn: 0.2643193	total: 69.7ms	remaining: 627ms
5:	learn: 0.2401075	total: 81.2ms	remaining: 596ms
6:	learn: 0.2328214	total: 91ms	remaining: 559ms
7:	learn: 0.2200712	total: 103ms	remaining: 539ms
8:	learn: 0.2154766	total: 113ms	remaining: 515ms
9:	learn: 0.2069499	total: 123ms	remaining: 494ms
10:	learn: 0.1964206	total: 134ms	remaining: 476ms
11:	learn: 0.1854377	total: 146ms	remaining: 461ms
12:	learn: 0.1773595	total: 157ms	remaining: 446ms
13:	learn: 0.1752377	total: 167ms	remaining: 431ms
14:	learn: 0.1733999	total: 178ms	remaining:

32:	learn: 0.1485643	total: 418ms	remaining: 215ms
33:	learn: 0.1469246	total: 430ms	remaining: 202ms
34:	learn: 0.1467580	total: 440ms	remaining: 189ms
35:	learn: 0.1466218	total: 450ms	remaining: 175ms
36:	learn: 0.1452725	total: 461ms	remaining: 162ms
37:	learn: 0.1450830	total: 470ms	remaining: 149ms
38:	learn: 0.1448089	total: 480ms	remaining: 136ms
39:	learn: 0.1446379	total: 491ms	remaining: 123ms
40:	learn: 0.1433640	total: 503ms	remaining: 110ms
41:	learn: 0.1431594	total: 513ms	remaining: 97.7ms
42:	learn: 0.1421189	total: 524ms	remaining: 85.4ms
43:	learn: 0.1419561	total: 534ms	remaining: 72.9ms
44:	learn: 0.1416579	total: 544ms	remaining: 60.4ms
45:	learn: 0.1403507	total: 556ms	remaining: 48.4ms
46:	learn: 0.1402423	total: 565ms	remaining: 36.1ms
47:	learn: 0.1401097	total: 576ms	remaining: 24ms
48:	learn: 0.1399906	total: 587ms	remaining: 12ms
49:	learn: 0.1390086	total: 597ms	remaining: 0us
32:	learn: 0.1485643	total: 418ms	remaining: 215ms
33:	learn: 0.1469246	total: 4

...

4:	learn: 0.3095585	total: 42.2ms	remaining: 380ms
5:	learn: 0.2903811	total: 49.2ms	remaining: 361ms
6:	learn: 0.2722538	total: 56.4ms	remaining: 346ms
7:	learn: 0.2576462	total: 63.7ms	remaining: 334ms
8:	learn: 0.2503478	total: 69.6ms	remaining: 317ms
9:	learn: 0.2357970	total: 76.5ms	remaining: 306ms
10:	learn: 0.2249824	total: 82.4ms	remaining: 292ms
11:	learn: 0.2167382	total: 88.4ms	remaining: 280ms
12:	learn: 0.2088138	total: 94.3ms	remaining: 268ms
13:	learn: 0.2009580	total: 99.6ms	remaining: 256ms
14:	learn: 0.1912810	total: 105ms	remaining: 245ms
15:	learn: 0.1896983	total: 111ms	remaining: 235ms
16:	learn: 0.1885233	total: 116ms	remaining: 225ms
17:	learn: 0.1859918	total: 121ms	remaining: 215ms
18:	learn: 0.1836511	total: 126ms	remaining: 206ms
19:	learn: 0.1830077	total: 132ms	remaining: 197ms
20:	learn: 0.1805430	total: 137ms	remaining: 189ms
21:	learn: 0.1782197	total: 142ms	remaining: 181ms
22:	learn: 0.1762340	total: 147ms	remaining: 173ms
23:	learn: 0.1757885	total:

38:	learn: 0.1594100	total: 215ms	remaining: 60.5ms
39:	learn: 0.1579443	total: 220ms	remaining: 54.9ms
40:	learn: 0.1576300	total: 224ms	remaining: 49.3ms
41:	learn: 0.1567902	total: 229ms	remaining: 43.7ms
42:	learn: 0.1565950	total: 234ms	remaining: 38.1ms
43:	learn: 0.1564320	total: 239ms	remaining: 32.5ms
44:	learn: 0.1557055	total: 244ms	remaining: 27.1ms
45:	learn: 0.1553144	total: 249ms	remaining: 21.7ms
46:	learn: 0.1541978	total: 254ms	remaining: 16.2ms
47:	learn: 0.1530205	total: 261ms	remaining: 10.9ms
48:	learn: 0.1525523	total: 267ms	remaining: 5.45ms
49:	learn: 0.1523181	total: 273ms	remaining: 0us
0:	learn: 0.4967656	total: 7.35ms	remaining: 360ms
1:	learn: 0.4195564	total: 13.9ms	remaining: 334ms
2:	learn: 0.3723401	total: 19.9ms	remaining: 311ms
3:	learn: 0.3363526	total: 27.5ms	remaining: 316ms
4:	learn: 0.3034832	total: 32.1ms	remaining: 289ms
38:	learn: 0.1594100	total: 215ms	remaining: 60.5ms
39:	learn: 0.1579443	total: 220ms	remaining: 54.9ms
40:	learn: 0.1576300

15:	learn: 0.2002517	total: 81.7ms	remaining: 174ms
16:	learn: 0.1963056	total: 87.8ms	remaining: 170ms
17:	learn: 0.1954078	total: 93ms	remaining: 165ms
18:	learn: 0.1944089	total: 98.1ms	remaining: 160ms
19:	learn: 0.1923055	total: 103ms	remaining: 155ms
20:	learn: 0.1900305	total: 108ms	remaining: 150ms
21:	learn: 0.1876461	total: 114ms	remaining: 145ms
22:	learn: 0.1868282	total: 120ms	remaining: 140ms
23:	learn: 0.1843179	total: 125ms	remaining: 135ms
24:	learn: 0.1821787	total: 130ms	remaining: 130ms
25:	learn: 0.1803496	total: 136ms	remaining: 125ms
26:	learn: 0.1787690	total: 141ms	remaining: 120ms
27:	learn: 0.1778862	total: 147ms	remaining: 115ms
28:	learn: 0.1760072	total: 152ms	remaining: 110ms
29:	learn: 0.1747529	total: 157ms	remaining: 105ms
30:	learn: 0.1734508	total: 162ms	remaining: 99.6ms
31:	learn: 0.1731961	total: 167ms	remaining: 94.2ms
32:	learn: 0.1722652	total: 172ms	remaining: 88.5ms
33:	learn: 0.1710426	total: 177ms	remaining: 83.1ms
34:	learn: 0.1707425	tota

10:	learn: 0.2302253	total: 62.9ms	remaining: 223ms
11:	learn: 0.2204694	total: 68.1ms	remaining: 216ms
12:	learn: 0.2108309	total: 74.3ms	remaining: 211ms
13:	learn: 0.2039533	total: 79.3ms	remaining: 204ms
14:	learn: 0.2027474	total: 84.2ms	remaining: 196ms
15:	learn: 0.2014288	total: 88.8ms	remaining: 189ms
16:	learn: 0.1979043	total: 93.3ms	remaining: 181ms
17:	learn: 0.1970432	total: 98ms	remaining: 174ms
18:	learn: 0.1964171	total: 102ms	remaining: 167ms
19:	learn: 0.1939345	total: 107ms	remaining: 161ms
20:	learn: 0.1916492	total: 112ms	remaining: 154ms
21:	learn: 0.1895874	total: 116ms	remaining: 148ms
22:	learn: 0.1887223	total: 121ms	remaining: 142ms
23:	learn: 0.1862679	total: 125ms	remaining: 136ms
24:	learn: 0.1843677	total: 130ms	remaining: 130ms
25:	learn: 0.1812185	total: 135ms	remaining: 124ms
26:	learn: 0.1798303	total: 139ms	remaining: 118ms
27:	learn: 0.1778183	total: 143ms	remaining: 113ms
28:	learn: 0.1754774	total: 148ms	remaining: 107ms
29:	learn: 0.1732239	tota

1:	learn: 0.4055472	total: 12.9ms	remaining: 309ms
2:	learn: 0.3556939	total: 19.6ms	remaining: 308ms
3:	learn: 0.3112961	total: 24.2ms	remaining: 278ms
4:	learn: 0.2883165	total: 28.7ms	remaining: 258ms
5:	learn: 0.2761855	total: 34.1ms	remaining: 250ms
6:	learn: 0.2679276	total: 38.5ms	remaining: 236ms
7:	learn: 0.2541808	total: 42.9ms	remaining: 225ms
8:	learn: 0.2417904	total: 48ms	remaining: 219ms
9:	learn: 0.2376267	total: 52.6ms	remaining: 210ms
10:	learn: 0.2287885	total: 57.1ms	remaining: 203ms
11:	learn: 0.2208120	total: 61.8ms	remaining: 196ms
12:	learn: 0.2189807	total: 66.6ms	remaining: 190ms
13:	learn: 0.2150532	total: 71.2ms	remaining: 183ms
14:	learn: 0.2116470	total: 75.9ms	remaining: 177ms
15:	learn: 0.2078798	total: 80.5ms	remaining: 171ms
16:	learn: 0.2062773	total: 84.8ms	remaining: 165ms
17:	learn: 0.2031010	total: 89.4ms	remaining: 159ms
18:	learn: 0.1980868	total: 94.1ms	remaining: 153ms
19:	learn: 0.1962775	total: 98.6ms	remaining: 148ms
20:	learn: 0.1930349	to

--- Visualisation ---

In [94]:
precision_scores= {
                    'Logistic Regression Precision:': precision_score(y_test, y_pred_lr, zero_division= 0),
                    'Decision Tree Precision:': precision_score(y_test, y_pred_dt, zero_division= 0),
                    'Tuned Decision Tree Precision:': precision_score(y_test, y_pred_tuned_dt, zero_division= 0),
                    'Random Forest Precision:': precision_score(y_test, y_pred_rf, zero_division= 0),
                    'Tuned Random Forest Precision:': precision_score(y_test, y_pred_tuned_rf, zero_division= 0),
                    'AdaBoost Precision:': precision_score(y_test, y_pred_ada, zero_division= 0),
                    'Tuned AdaBoost Precision:': precision_score(y_test, y_pred_tuned_ada, zero_division= 0),
                    'GradientBoosting Precision:': precision_score(y_test, y_pred_grb, zero_division= 0),
                    'Tuned GradientBoosting Precision:': precision_score(y_test, y_pred_tuned_grb, zero_division= 0),
                    'XGB Precision:': precision_score(y_test, y_pred_xgb, zero_division= 0),
                    'Tuned XGB Precision:': precision_score(y_test, y_pred_tuned_xgb, zero_division= 0),
                    'LGBM Precision:': precision_score(y_test, y_pred_lgm, zero_division= 0),
                    'Tuned LGBM Precision:': precision_score(y_test, y_pred_tuned_lgm, zero_division= 0),
                    'CatBoost Precision:': precision_score(y_test, y_pred_cat, zero_division= 0),
                    'Tuned CatBoost Precision:': precision_score(y_test, y_pred_tuned_cat, zero_division= 0)
                  }

rfe_precision= pd.DataFrame(list(precision_scores.items()), columns= ['Model', 'Precision Score'])
rfe_precision= rfe_precision.sort_values(by= 'Precision Score', ascending=False)
print(rfe_precision)

                                Model  Precision Score
11                    LGBM Precision:         0.509934
13                CatBoost Precision:         0.496350
14          Tuned CatBoost Precision:         0.493827
12              Tuned LGBM Precision:         0.486911
9                      XGB Precision:         0.457895
8   Tuned GradientBoosting Precision:         0.440433
6           Tuned AdaBoost Precision:         0.435262
10               Tuned XGB Precision:         0.421429
7         GradientBoosting Precision:         0.395230
4      Tuned Random Forest Precision:         0.365617
5                 AdaBoost Precision:         0.347743
2      Tuned Decision Tree Precision:         0.319672
3            Random Forest Precision:         0.317025
1            Decision Tree Precision:         0.261968
0      Logistic Regression Precision:         0.241969
                                Model  Precision Score
11                    LGBM Precision:         0.509934
13        

In [95]:
accuracy_scores= {
                    'Logistic Regression Accuracy:': accuracy_score(y_test, y_pred_lr),
                    'Decision Tree Accuracy:': accuracy_score(y_test, y_pred_dt),
                    'Tuned Decision Tree Accuracy:': accuracy_score(y_test, y_pred_tuned_dt),
                    'Random Forest Accuracy:': accuracy_score(y_test, y_pred_rf),
                    'Tuned Random Forest Accuracy:': accuracy_score(y_test, y_pred_tuned_rf),
                    'AdaBoost Accuracy:': accuracy_score(y_test, y_pred_ada),
                    'Tuned AdaBoost Accuracy:': accuracy_score(y_test, y_pred_tuned_ada),
                    'GradientBoosting Accuracy:': accuracy_score(y_test, y_pred_grb),
                    'Tuned GradientBoosting Accuracy:': accuracy_score(y_test, y_pred_tuned_grb),
                    'XGB Accuracy:': accuracy_score(y_test, y_pred_xgb),
                    'Tuned XGB Accuracy:': accuracy_score(y_test, y_pred_tuned_xgb),
                    'LGBM Accuracy:': accuracy_score(y_test, y_pred_lgm),
                    'Tuned LGBM Accuracy:': accuracy_score(y_test, y_pred_tuned_lgm),
                    'CatBoost Accuracy:': accuracy_score(y_test, y_pred_cat),
                    'Tuned CatBoost Accuracy:': accuracy_score(y_test, y_pred_tuned_cat)
                  }

rfe_accuracy= pd.DataFrame(list(accuracy_scores.items()), columns= ['Model', 'Accuracy Score'])
rfe_accuracy= rfe_accuracy.sort_values(by= 'Accuracy Score', ascending=False)
print(rfe_accuracy)

                               Model  Accuracy Score
11                    LGBM Accuracy:        0.903595
13                CatBoost Accuracy:        0.903171
14          Tuned CatBoost Accuracy:        0.903065
12              Tuned LGBM Accuracy:        0.902747
9                      XGB Accuracy:        0.901580
8   Tuned GradientBoosting Accuracy:        0.899777
10               Tuned XGB Accuracy:        0.898611
6           Tuned AdaBoost Accuracy:        0.898293
4      Tuned Random Forest Accuracy:        0.891505
7         GradientBoosting Accuracy:        0.890232
2      Tuned Decision Tree Accuracy:        0.884611
3            Random Forest Accuracy:        0.883445
5                 AdaBoost Accuracy:        0.869657
1            Decision Tree Accuracy:        0.865309
0      Logistic Regression Accuracy:        0.743133
                               Model  Accuracy Score
11                    LGBM Accuracy:        0.903595
13                CatBoost Accuracy:        0.

In [96]:
auc_scores= {
                    'Logistic Regression AUC:': roc_auc_score(y_test, y_pred_prob_lr),
                    'Decision Tree AUC:': roc_auc_score(y_test, y_pred_prob_dt),
                    'Tuned Decision Tree AUC:': roc_auc_score(y_test, y_pred_prob_tuned_dt),
                    'Random Forest AUC:': roc_auc_score(y_test, y_pred_prob_rf),
                    'Tuned Random Forest AUC:': roc_auc_score(y_test, y_pred_prob_tuned_rf),
                    'AdaBoost AUC:': roc_auc_score(y_test, y_pred_prob_ada),
                    'Tuned AdaBoost AUC:': roc_auc_score(y_test, y_pred_prob_tuned_ada),
                    'GradientBoosting AUC:': roc_auc_score(y_test, y_pred_prob_grb),
                    'Tuned GradientBoosting AUC:': roc_auc_score(y_test, y_pred_prob_tuned_grb),
                    'XGB AUC:': roc_auc_score(y_test, y_pred_prob_xgb),
                    'Tuned XGB AUC:': roc_auc_score(y_test, y_pred_prob_tuned_xgb),
                    'LGBM AUC:': roc_auc_score(y_test, y_pred_prob_lgm),
                    'Tuned LGBM AUC:': roc_auc_score(y_test, y_pred_prob_tuned_lgm),
                    'CatBoost AUC:': roc_auc_score(y_test, y_pred_prob_cat),
                    'Tuned CatBoost AUC:': roc_auc_score(y_test, y_pred_prob_tuned_cat)
                  }

rfe_auc= pd.DataFrame(list(auc_scores.items()), columns= ['Model', 'AUC Score'])
rfe_auc= rfe_auc.sort_values(by= 'AUC Score', ascending=False)
print(rfe_auc)

                          Model  AUC Score
0      Logistic Regression AUC:   0.837566
5                 AdaBoost AUC:   0.824093
7         GradientBoosting AUC:   0.821224
8   Tuned GradientBoosting AUC:   0.819407
10               Tuned XGB AUC:   0.816064
11                    LGBM AUC:   0.808210
12              Tuned LGBM AUC:   0.807366
14          Tuned CatBoost AUC:   0.806100
9                      XGB AUC:   0.804016
6           Tuned AdaBoost AUC:   0.803449
13                CatBoost AUC:   0.802068
4      Tuned Random Forest AUC:   0.772369
3            Random Forest AUC:   0.753936
2      Tuned Decision Tree AUC:   0.732111
1            Decision Tree AUC:   0.592985
                          Model  AUC Score
0      Logistic Regression AUC:   0.837566
5                 AdaBoost AUC:   0.824093
7         GradientBoosting AUC:   0.821224
8   Tuned GradientBoosting AUC:   0.819407
10               Tuned XGB AUC:   0.816064
11                    LGBM AUC:   0.808210
12         